# Consignes

Intégrer le fichier USvideos.csv qui représente un ensemble de 8000 vidéos Youtube. 

Merger le fichier US_category_id.json pour récupérer le nom des catégories. Il conviendra de bien spécifier l'ID du document.


# Questions 
- 1) Récupérer toutes les vidéos de la chaîne Apple.
- 2) Compter le nombre de catégories différentes
- 3) Si vous ne l'avez pas déjà fait, découper les tags en listes et mettre à jour les tags de chacun des documents avec une requête update.
- 4) Récupérer les vidéos les plus vues.
- 5) Compter le nombre moyen de vues en fonction de la catégorie.
- 6) Récupérer les chaines Youtube avec la plus grande moyenne de likes.

In [1]:
import pandas as pd
import pymongo

In [19]:
client = pymongo.MongoClient("mongo")
database = client['exercices']
collection = database['youtube']

In [14]:
df_youtube = pd.read_csv("./data/USvideos.csv")
df_youtube.head(2)

video_id                                              title  \
0  XpVt6Z1Gjjo  1 YEAR OF VLOGGING -- HOW LOGAN PAUL CHANGED Y...   
1  K4wEI5zhHB0            iPhone X — Introducing iPhone X — Apple   

      channel_title  category_id  \
0  Logan Paul Vlogs           24   
1             Apple           28   

                                                tags    views   likes  \
0  logan paul vlog|logan paul|logan|paul|olympics...  4394029  320053   
1  Apple|iPhone 10|iPhone Ten|iPhone|Portrait Lig...  7860119  185853   

   dislikes  comment_total                                  thumbnail_link  \
0      5931          46245  https://i.ytimg.com/vi/XpVt6Z1Gjjo/default.jpg   
1     26679              0  https://i.ytimg.com/vi/K4wEI5zhHB0/default.jpg   

    date  
0  13.09  
1  13.09

## Question 0

### Netoyer les données

In [31]:
df_category = pd.read_json("./data/US_category_id.json",orient="records")
df_category["items"]

0     {'kind': 'youtube#videoCategory', 'etag': '"m2...
1     {'kind': 'youtube#videoCategory', 'etag': '"m2...
2     {'kind': 'youtube#videoCategory', 'etag': '"m2...
3     {'kind': 'youtube#videoCategory', 'etag': '"m2...
4     {'kind': 'youtube#videoCategory', 'etag': '"m2...
5     {'kind': 'youtube#videoCategory', 'etag': '"m2...
6     {'kind': 'youtube#videoCategory', 'etag': '"m2...
7     {'kind': 'youtube#videoCategory', 'etag': '"m2...
8     {'kind': 'youtube#videoCategory', 'etag': '"m2...
9     {'kind': 'youtube#videoCategory', 'etag': '"m2...
10    {'kind': 'youtube#videoCategory', 'etag': '"m2...
11    {'kind': 'youtube#videoCategory', 'etag': '"m2...
12    {'kind': 'youtube#videoCategory', 'etag': '"m2...
13    {'kind': 'youtube#videoCategory', 'etag': '"m2...
14    {'kind': 'youtube#videoCategory', 'etag': '"m2...
15    {'kind': 'youtube#videoCategory', 'etag': '"m2...
16    {'kind': 'youtube#videoCategory', 'etag': '"m2...
17    {'kind': 'youtube#videoCategory', 'etag': 

In [33]:
df_test = df_category.copy()
df_test.head()

kind  \
0  youtube#videoCategoryListResponse   
1  youtube#videoCategoryListResponse   
2  youtube#videoCategoryListResponse   
3  youtube#videoCategoryListResponse   
4  youtube#videoCategoryListResponse   

                                                etag  \
0  "m2yskBQFythfE4irbTIeOgYYfBU/S730Ilt-Fi-emsQJv...   
1  "m2yskBQFythfE4irbTIeOgYYfBU/S730Ilt-Fi-emsQJv...   
2  "m2yskBQFythfE4irbTIeOgYYfBU/S730Ilt-Fi-emsQJv...   
3  "m2yskBQFythfE4irbTIeOgYYfBU/S730Ilt-Fi-emsQJv...   
4  "m2yskBQFythfE4irbTIeOgYYfBU/S730Ilt-Fi-emsQJv...   

                                               items  
0  {'kind': 'youtube#videoCategory', 'etag': '"m2...  
1  {'kind': 'youtube#videoCategory', 'etag': '"m2...  
2  {'kind': 'youtube#videoCategory', 'etag': '"m2...  
3  {'kind': 'youtube#videoCategory', 'etag': '"m2...  
4  {'kind': 'youtube#videoCategory', 'etag': '"m2...

In [39]:
df_test["items"]

0     {'kind': 'youtube#videoCategory', 'etag': '"m2...
1     {'kind': 'youtube#videoCategory', 'etag': '"m2...
2     {'kind': 'youtube#videoCategory', 'etag': '"m2...
3     {'kind': 'youtube#videoCategory', 'etag': '"m2...
4     {'kind': 'youtube#videoCategory', 'etag': '"m2...
5     {'kind': 'youtube#videoCategory', 'etag': '"m2...
6     {'kind': 'youtube#videoCategory', 'etag': '"m2...
7     {'kind': 'youtube#videoCategory', 'etag': '"m2...
8     {'kind': 'youtube#videoCategory', 'etag': '"m2...
9     {'kind': 'youtube#videoCategory', 'etag': '"m2...
10    {'kind': 'youtube#videoCategory', 'etag': '"m2...
11    {'kind': 'youtube#videoCategory', 'etag': '"m2...
12    {'kind': 'youtube#videoCategory', 'etag': '"m2...
13    {'kind': 'youtube#videoCategory', 'etag': '"m2...
14    {'kind': 'youtube#videoCategory', 'etag': '"m2...
15    {'kind': 'youtube#videoCategory', 'etag': '"m2...
16    {'kind': 'youtube#videoCategory', 'etag': '"m2...
17    {'kind': 'youtube#videoCategory', 'etag': 

In [65]:
df_test2 = df_test["items"].apply(pd.Series)
df_test3 = pd.concat([df_test2.drop(["snippet"],axis=1),df_test2["snippet"].apply(pd.Series)], axis=1)
print(df_test3.columns)
df_test3.head(25)

Index(['kind', 'etag', 'id', 'channelId', 'title', 'assignable'], dtype='object')


kind                                               etag  \
0   youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/Xy1mB4_yLrHy_BmKm...   
1   youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/UZ1oLIIz2dxIhO45Z...   
2   youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/nqRIq97-xe5XRZTxb...   
3   youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/HwXKamM1Q20q9BN-o...   
4   youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/9GQMSRjrZdHeb1OEM...   
5   youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/FJwVpGCVZ1yiJrqZb...   
6   youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/M-3iD9dwK7YJCafRf...   
7   youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/WmA0qYEfjWsAoyJFS...   
8   youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/EapFaGYG7K0StIXVf...   
9   youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/xId8RX7vRN8rqkbYZ...   
10  youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/G9LHzQmx44rX2S5ya...   
11  youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/UVB9oxX2Bvqa_w_y3...   
12  youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/QiLK0ZIrFoORdk_g2...   
13  youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/r6Ck6Z0_L0rG37VJQ...   
14  youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/EoYkczo9I3RCf96Rv...   
15  youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/w5HjcTD82G_XA3xBc...   
16  youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/SalkJoBWq_smSEqiA...   
17  youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/lL7uWDr_071CHxifj...   
18  youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/WnuVfjO-PyFLO7NTR...   
19  youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/ctpH2hGA_UZ3volJT...   
20  youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/L0kR3-g1BAo5UD1PL...   
21  youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/pUZOAC_s9sfiwar63...   
22  youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/Xb5JLhtyNRN3AQq02...   
23  youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/u8WXzF4HIhtEi805_...   
24  youtube#videoCategory  "m2yskBQFythfE4irbTIeOgYYfBU/D04PP4Gr7wc4IV_O9...   

    id                 channelId                  title  assignable  
0    1  UCBR8-60-B28hp2BmDPdntcQ       Film & Animation        True  
1    2  UCBR8-60-B28hp2BmDPdntcQ       Autos & Vehicles        True  
2   10  UCBR8-60-B28hp2BmDPdntcQ                  Music        True  
3   15  UCBR8-60-B28hp2BmDPdntcQ         Pets & Animals        True  
4   17  UCBR8-60-B28hp2BmDPdntcQ                 Sports        True  
5   18  UCBR8-60-B28hp2BmDPdntcQ           Short Movies       False  
6   19  UCBR8-60-B28hp2BmDPdntcQ        Travel & Events        True  
7   20  UCBR8-60-B28hp2BmDPdntcQ                 Gaming        True  
8   21  UCBR8-60-B28hp2BmDPdntcQ          Videoblogging       False  
9   22  UCBR8-60-B28hp2BmDPdntcQ         People & Blogs        True  
10  23  UCBR8-60-B28hp2BmDPdntcQ                 Comedy        True  
11  24  UCBR8-60-B28hp2BmDPdntcQ          Entertainment        True  
12  25  UCBR8-60-B28hp2BmDPdntcQ        News & Politics        True  
13  26  UCBR8-60-B28hp2BmDPdntcQ          Howto & Style        True  
14  27  UCBR8-60-B28hp2BmDPdntcQ              Education        True  
15  28  UCBR8-60-B28hp2BmDPdntcQ   Science & Technology        True  
16  29  UCBR8-60-B28hp2BmDPdntcQ  Nonprofits & Activism        True  
17  30  UCBR8-60-B28hp2BmDPdntcQ                 Movies       False  
18  31  UCBR8-60-B28hp2BmDPdntcQ        Anime/Animation       False  
19  32  UCBR8-60-B28hp2BmDPdntcQ       Action/Adventure       False  
20  33  UCBR8-60-B28hp2BmDPdntcQ               Classics       False  
21  34  UCBR8-60-B28hp2BmDPdntcQ                 Comedy       False  
22  35  UCBR8-60-B28hp2BmDPdntcQ            Documentary       False  
23  36  UCBR8-60-B28hp2BmDPdntcQ                  Drama       False  
24  37  UCBR8-60-B28hp2BmDPdntcQ                 Family       False

In [66]:
df_test3 = df_test3.rename(columns={"id":"category_id"})

In [25]:
df_youtube.head(25)

video_id                                              title  \
0   XpVt6Z1Gjjo  1 YEAR OF VLOGGING -- HOW LOGAN PAUL CHANGED Y...   
1   K4wEI5zhHB0            iPhone X — Introducing iPhone X — Apple   
2   cLdxuaxaQwc                                        My Response   
3   WYYvHb03Eog                          Apple iPhone X first look   
4   sjlHnJvXdQs                                  iPhone X (parody)   
5   cMKX2tE5Luk    The Disaster Artist | Official Trailer HD | A24   
6   8wNr-NQImFg       The Check In: HUD, Ben Carson and Hurricanes   
7   _HTXMhKWqnA                   iPhone X Impressions & Hands On!   
8   _ANP3HR1jsM                         ATTACKED BY A POLICE DOG!!   
9   zgLtEob6X-Q                 Honest Trailers - The Mummy (2017)   
10  Ayb_2qbZHm4                                Honest College Tour   
11  CsdzflTXBVQ  Best Floyd Mayweather Interview | Awkward Puppets   
12  l864IBj7cgw  Jennifer Lawrence Challenges Jimmy to an Axe T...   
13  4MkC65emkG4  Hand In Hand A Benefit For Hurricane Relief | MTV   
14  vu_9muoxT50  Colin Cloud: Mind Reader Predicts Your Tweets ...   
15  1L7JFN7tQLs    iPhone X Hands on - Everything you need to know   
16  ZQK1F0wz6z4                          What Do You Want to Eat?!   
17  T_PuZBdT2iM  getting into a conversation in a language you ...   
18  w8fAellnPns  Juicy Chicken Breast - You Suck at Cooking (ep...   
19  UCrBICYM0yM  Downsizing (2017) - Official Trailer - Paramou...   
20  -Ifnaxi2LQg          Fergie - You Already Know ft. Nicki Minaj   
21  B7YaMkCl3XA      Hurricane Irma death toll rises to 10 in Cuba   
22  5ywKal6-anc  Gigi Hadid Loses High Heel During Fashion Week...   
23  4Yue-q9Jdbk     SUPERFRUIT REACTS TO TEENS REACT TO SUPERFRUIT   
24  JhA1Wi9mrns         Kid Rock - Tennessee Mountain Top [Lyrics]   

                             channel_title  category_id  \
0                         Logan Paul Vlogs           24   
1                                    Apple           28   
2                                PewDiePie           22   
3                                The Verge           28   
4                               jacksfilms           23   
5                                      A24            1   
6              Late Night with Seth Meyers           23   
7                         Marques Brownlee           28   
8                         RomanAtwoodVlogs           22   
9                           Screen Junkies            1   
10                            CollegeHumor           23   
11                         Awkward Puppets           23   
12  The Tonight Show Starring Jimmy Fallon           23   
13                                     MTV           24   
14                    America's Got Talent           24   
15                       Jonathan Morrison           28   
16                     Wong Fu Productions           24   
17                                   ProZD            1   
18                     You Suck At Cooking           26   
19                      Paramount Pictures            1   
20                              FergieVEVO           10   
21                      Al Jazeera English           25   
22                                     TMZ           24   
23                              SUPERFRUIT           24   
24                                Kid Rock           10   

                                                 tags    views   likes  \
0   logan paul vlog|logan paul|logan|paul|olympics...  4394029  320053   
1   Apple|iPhone 10|iPhone Ten|iPhone|Portrait Lig...  7860119  185853   
2                                              [none]  5845909  576597   
3   apple iphone x hands on|Apple iPhone X|iPhone ...  2642103   24975   
4   jacksfilms|parody|parodies|iphone|iphone x|iph...  1168130   96666   
5   a24|a24 films|a24 trailers|independent films|t...  1311445   34507   
6   Late night|Seth Meyers|check in|hud|Ben Carson...   666169    9985   
7   iPhone X|iphone x|iphone 10|iPhone X impressio...  1728

In [67]:
df_test3.dtypes

kind           object
etag           object
category_id    object
channelId      object
title          object
assignable       bool
dtype: object

In [68]:
df_test3 = df_test3.astype({"category_id":"int64"})
df_test3.dtypes

kind           object
etag           object
category_id     int64
channelId      object
title          object
assignable       bool
dtype: object

In [61]:
df_youtube.dtypes

video_id           object
title              object
channel_title      object
category_id         int64
tags               object
views               int64
likes               int64
dislikes            int64
comment_total       int64
thumbnail_link     object
date              float64
dtype: object

In [69]:
df = pd.merge(df_youtube,df_test3, how="inner", left_on="category_id",right_on="category_id")

In [71]:
df = df.rename(columns={"title_y":"category"})
df.head(25)

video_id                                            title_x  \
0   XpVt6Z1Gjjo  1 YEAR OF VLOGGING -- HOW LOGAN PAUL CHANGED Y...   
1   4MkC65emkG4  Hand In Hand A Benefit For Hurricane Relief | MTV   
2   vu_9muoxT50  Colin Cloud: Mind Reader Predicts Your Tweets ...   
3   ZQK1F0wz6z4                          What Do You Want to Eat?!   
4   5ywKal6-anc  Gigi Hadid Loses High Heel During Fashion Week...   
5   4Yue-q9Jdbk     SUPERFRUIT REACTS TO TEENS REACT TO SUPERFRUIT   
6   1ZNZY-gd3K0  Joe Arpaio: Last Week Tonight with John Oliver...   
7   JO7X9ZPoAp8                       Blind People Describe Beauty   
8   oDIDZ9EmQfA                 Jumping Through Impossible Shapes!   
9   zAtHxJvSczA  Does Maggie Gyllenhaal Have Taylor Swift’s Sca...   
10  qJJHhVf3_ZM  Gwyneth Paltrow Crashes James' Goop Magazine Rant   
11  Ez95rPffd8k  Jim Carrey's Bizarre Fashion Week Interview | ...   
12  GpAuCG6iUcA                   Fifty Shades Freed - Teaser [HD]   
13  -JmNKGfFj7w  Jim Carrey Sounds Off on Icons and More at NYF...   
14  aZkqHx5uri4  Can You Assume Sexuality Based on a First Impr...   
15  1Sm8A-u1vIA                    LIVE TRACKING OF HURRICANE IRMA   
16  amds5iNvFD4  I Gave Myself A Celebrity Hair Transformation ...   
17  Pp19TkIU_fw            Life of Kylie Recap Season 1, Ep.7 | E!   
18  u6iVspBWzZU         what is derealisation / depersonalisation?   
19  Mq9dxmh6JiE                FENTY BEAUTY by RIHANNA FULL REVIEW   
20  jehAZhrI7oA                                  IT - SPOILER Talk   
21  Alp_a88C8dY         Stephen King's IT - What's the Difference?   
22  MmAL1EOkLUo                     SVU 9.11 Opener Dedication.wmv   
23  WAwRqecvMSY              ROASTING YOUTUBERS' NAILS (nail diss)   
24  uAipi4V5g34           Dancing in 80's Movies Supercut - Vol. 2   

                              channel_title  category_id  \
0                          Logan Paul Vlogs           24   
1                                       MTV           24   
2                      America's Got Talent           24   
3                       Wong Fu Productions           24   
4                                       TMZ           24   
5                                SUPERFRUIT           24   
6                           LastWeekTonight           24   
7                            WatchCut Video           24   
8                              Rclbeauty101           24   
9   Watch What Happens Live with Andy Cohen           24   
10     The Late Late Show with James Corden           24   
11                                  E! News           24   
12                             Fifty Shades           24   
13              E! Live from the Red Carpet           24   
14                              SoulPancake           24   
15                          ABC Action News           24   
16                           Michelle Khare           24   
17                         E! Entertainment           24   
18                            doddlevloggle           24   
19                            James Charles           24   
20                             Jeremy Jahns           24   
21                                  CineFix           24   
22                           DarthLucifer08           24   
23                        Simply Nailogical           24   
24                             Robert Jones           24   

                                                 tags    views   likes  \
0   logan paul vlog|logan paul|logan|paul|olympics...  4394029  320053   
1   mtv|video|online|official|tv|television|watch|...   274358    9215   
2   America's Got Talent 2017|america's got talent...   473691   14740   
3   panda|what should we eat|buzzfeed|comedy|boyfr...   282858   14870   
4   TMZ2016FS11221|TMZ|Hollywood|Celebrity|Enterta...   703750    2921   
5   superfruit|super|fruit|scott|hoying|mitch|gras...   255967   21817   
6   last week tonight joe arpaio|joe arpaio|john o...  3298456   65730   
7   blind people|buzzfeed|beauty|

### Importer les données

In [73]:
dict_df = df.to_dict(orient='record')

In [75]:
collection.insert_many(dict_df)

In [80]:
database.collection_names()

<ipython-input-80-40f0ffef35b3>:1: DeprecationWarning: collection_names is deprecated. Use list_collection_names instead.
  database.collection_names()


['youtube']

In [81]:
collection.find_one()

{'_id': ObjectId('5fc5007c350898a3d9107158'),
 'video_id': 'XpVt6Z1Gjjo',
 'title_x': '1 YEAR OF VLOGGING -- HOW LOGAN PAUL CHANGED YOUTUBE FOREVER!',
 'channel_title': 'Logan Paul Vlogs',
 'category_id': 24,
 'tags': 'logan paul vlog|logan paul|logan|paul|olympics|logan paul youtube|vlog|daily|comedy|hollywood|parrot|maverick|bird|maverick clothes|diamond play button|logan paul diamond play button|10M subscribers|logan paul 1 year vlogging|1 year vlog|dwarf mamba play button|logan paul history|youtube history|10M|10M plaque|youtube button|diamond button|logang|logang 4 life',
 'views': 4394029,
 'likes': 320053,
 'dislikes': 5931,
 'comment_total': 46245,
 'thumbnail_link': 'https://i.ytimg.com/vi/XpVt6Z1Gjjo/default.jpg',
 'date': 13.09,
 'kind': 'youtube#videoCategory',
 'etag': '"m2yskBQFythfE4irbTIeOgYYfBU/UVB9oxX2Bvqa_w_y3vXSLVK5E_s"',
 'channelId': 'UCBR8-60-B28hp2BmDPdntcQ',
 'category': 'Entertainment',
 'assignable': True}

## Question 1  

In [82]:
cur = collection.find({"channel_title":"Apple"})
for video in cur :
    print("-----")
    print(video)

-----
{'_id': ObjectId('5fc5007c350898a3d9107799'), 'video_id': 'K4wEI5zhHB0', 'title_x': 'iPhone X — Introducing iPhone X — Apple', 'channel_title': 'Apple', 'category_id': 28, 'tags': 'Apple|iPhone 10|iPhone Ten|iPhone|Portrait Lighting|A11 Bionic|augmented reality|emoji|animoji|Face ID|Apple Pay|camera|smartphone', 'views': 7860119, 'likes': 185853, 'dislikes': 26679, 'comment_total': 0, 'thumbnail_link': 'https://i.ytimg.com/vi/K4wEI5zhHB0/default.jpg', 'date': 13.09, 'kind': 'youtube#videoCategory', 'etag': '"m2yskBQFythfE4irbTIeOgYYfBU/w5HjcTD82G_XA3xBctS30zS-JpQ"', 'channelId': 'UCBR8-60-B28hp2BmDPdntcQ', 'category': 'Science & Technology', 'assignable': True}
-----
{'_id': ObjectId('5fc5007c350898a3d91077a9'), 'video_id': 'K4wEI5zhHB0', 'title_x': 'iPhone X — Introducing iPhone X — Apple', 'channel_title': 'Apple', 'category_id': 28, 'tags': 'Apple|iPhone 10|iPhone Ten|iPhone|Portrait Lighting|A11 Bionic|augmented reality|emoji|animoji|Face ID|Apple Pay|camera|smartphone', 'vie

## Question 2

In [93]:
len(collection.distinct('category_id'))

16

## Question 3

In [104]:
cursor = collection.find({},{"tags"})
for i in cursor :
    collection.update_one({"_id":i["_id"]},{'$set':{'tags':i['tags'].split('|') }})

AttributeError: 'list' object has no attribute 'split'

In [103]:
cur = collection.find()
for video in cur :
    print("-----")
    print(video)

-----
{'_id': ObjectId('5fc5007c350898a3d9107158'), 'video_id': 'XpVt6Z1Gjjo', 'title_x': '1 YEAR OF VLOGGING -- HOW LOGAN PAUL CHANGED YOUTUBE FOREVER!', 'channel_title': 'Logan Paul Vlogs', 'category_id': 24, 'tags': ['logan paul vlog', 'logan paul', 'logan', 'paul', 'olympics', 'logan paul youtube', 'vlog', 'daily', 'comedy', 'hollywood', 'parrot', 'maverick', 'bird', 'maverick clothes', 'diamond play button', 'logan paul diamond play button', '10M subscribers', 'logan paul 1 year vlogging', '1 year vlog', 'dwarf mamba play button', 'logan paul history', 'youtube history', '10M', '10M plaque', 'youtube button', 'diamond button', 'logang', 'logang 4 life'], 'views': 4394029, 'likes': 320053, 'dislikes': 5931, 'comment_total': 46245, 'thumbnail_link': 'https://i.ytimg.com/vi/XpVt6Z1Gjjo/default.jpg', 'date': 13.09, 'kind': 'youtube#videoCategory', 'etag': '"m2yskBQFythfE4irbTIeOgYYfBU/UVB9oxX2Bvqa_w_y3vXSLVK5E_s"', 'channelId': 'UCBR8-60-B28hp2BmDPdntcQ', 'category': 'Entertainment', 

{'_id': ObjectId('5fc5007c350898a3d9107313'), 'video_id': 'QAT8fXZI0b0', 'title_x': 'Watsky- Yes Britannia [x Infinity]', 'channel_title': 'WATSKY!', 'category_id': 24, 'tags': ['Watsky', 'Yes Brittania', 'x Infinity'], 'views': 52301, 'likes': 4069, 'dislikes': 29, 'comment_total': 400, 'thumbnail_link': 'https://i.ytimg.com/vi/QAT8fXZI0b0/default.jpg', 'date': 24.09, 'kind': 'youtube#videoCategory', 'etag': '"m2yskBQFythfE4irbTIeOgYYfBU/UVB9oxX2Bvqa_w_y3vXSLVK5E_s"', 'channelId': 'UCBR8-60-B28hp2BmDPdntcQ', 'category': 'Entertainment', 'assignable': True}
-----
{'_id': ObjectId('5fc5007c350898a3d9107314'), 'video_id': '_o8vb1BA_c0', 'title_x': 'Twin Swap Prank On My Boyfriend with The Merrell Twins!', 'channel_title': 'Rclbeauty101', 'category_id': 24, 'tags': ['twin swap prank on my boyfriend', 'rclbeauty101', 'the undervlogs', 'the under vlogs', 'theundervlogs', 'under vlogs', 'undervlogs', 'rachel levin', 'tyler regan', 'caoimhe', 'caoimhe morris', 'derek kildall', 'rachel', 'tyle

-----
{'_id': ObjectId('5fc5007c350898a3d910759f'), 'video_id': 'bpDylTwwunc', 'title_x': 'Demi Lovato: Simply Complicated - Official Trailer - Coming to YouTube Oct 17th', 'channel_title': 'Demi Lovato', 'category_id': 24, 'tags': ['Demi Lovato'], 'views': 385218, 'likes': 30765, 'dislikes': 273, 'comment_total': 1271, 'thumbnail_link': 'https://i.ytimg.com/vi/bpDylTwwunc/default.jpg', 'date': 11.1, 'kind': 'youtube#videoCategory', 'etag': '"m2yskBQFythfE4irbTIeOgYYfBU/UVB9oxX2Bvqa_w_y3vXSLVK5E_s"', 'channelId': 'UCBR8-60-B28hp2BmDPdntcQ', 'category': 'Entertainment', 'assignable': True}
-----
{'_id': ObjectId('5fc5007c350898a3d91075a0'), 'video_id': 'J5b_-TZwQ0I', 'title_x': 'Confederacy: Last Week Tonight with John Oliver (HBO)', 'channel_title': 'LastWeekTonight', 'category_id': 24, 'tags': ['last week tonight confederacy', 'john oliver confederacy'], 'views': 4097718, 'likes': 119045, 'dislikes': 10210, 'comment_total': 26053, 'thumbnail_link': 'https://i.ytimg.com/vi/J5b_-TZwQ0I/

{'_id': ObjectId('5fc5007c350898a3d91077e2'), 'video_id': 'a6y01PSb6qU', 'title_x': "The Strangest Sights Cassini Saw: Postcards From Saturn | NPR's SKUNK BEAR", 'channel_title': 'Skunk Bear', 'category_id': 28, 'tags': ['cassini', 'nasa', 'saturn', 'rings', 'titan', 'iapetus', 'mimas', 'daphnis', 'ripple', 'crash into saturn', 'huygens', 'enceladus', 'mission', 'launch', 'why', 'satellite', 'images', 'photos', 'hexagon', 'plume', 'discovery', 'spacecraft', 'probe', 'what is cassini', 'pictures', 'rings of saturn', 'cassini images', 'cassini pictures', 'cassini dive', 'cassini footage'], 'views': 138958, 'likes': 1227, 'dislikes': 15, 'comment_total': 107, 'thumbnail_link': 'https://i.ytimg.com/vi/a6y01PSb6qU/default.jpg', 'date': 17.09, 'kind': 'youtube#videoCategory', 'etag': '"m2yskBQFythfE4irbTIeOgYYfBU/w5HjcTD82G_XA3xBctS30zS-JpQ"', 'channelId': 'UCBR8-60-B28hp2BmDPdntcQ', 'category': 'Science & Technology', 'assignable': True}
-----
{'_id': ObjectId('5fc5007c350898a3d91077e3'), '

{'_id': ObjectId('5fc5007c350898a3d91079d7'), 'video_id': '9HIkG6vMk6E', 'title_x': 'WELCOME BABY TAIKA!', 'channel_title': 'Bart & Geo', 'category_id': 22, 'tags': ['geo antoinette', 'geovanna', 'bart kwan', 'relationship', 'advice', 'boyfriend', 'girlfriend'], 'views': 362844, 'likes': 30831, 'dislikes': 140, 'comment_total': 5376, 'thumbnail_link': 'https://i.ytimg.com/vi/9HIkG6vMk6E/default.jpg', 'date': 16.09, 'kind': 'youtube#videoCategory', 'etag': '"m2yskBQFythfE4irbTIeOgYYfBU/xId8RX7vRN8rqkbYZbNIytUQDRo"', 'channelId': 'UCBR8-60-B28hp2BmDPdntcQ', 'category': 'People & Blogs', 'assignable': True}
-----
{'_id': ObjectId('5fc5007c350898a3d91079d8'), 'video_id': 'cNgT8qEQJ3w', 'title_x': 'Alexa: Guess My Number', 'channel_title': 'Norm Krumpe', 'category_id': 22, 'tags': ['alexa', 'amazon', 'programming', 'echo'], 'views': 840615, 'likes': 9275, 'dislikes': 820, 'comment_total': 850, 'thumbnail_link': 'https://i.ytimg.com/vi/cNgT8qEQJ3w/default.jpg', 'date': 16.09, 'kind': 'youtub

{'_id': ObjectId('5fc5007c350898a3d9107bcd'), 'video_id': 'rWKz0ZC_G6U', 'title_x': 'DAY TO DEAD HALLOWEEN DRUGSTORE MAKEUP TUTORIAL | JAMIE GENEVIEVE', 'channel_title': 'Jamie Genevieve', 'category_id': 22, 'tags': ['jamie genevieve', 'bblogger', 'youtuber', 'makeup', 'tutorial', 'how to', 'vlog', 'makeup tutorial', 'day to night', 'day to dead', 'halloween makeup', 'halloween makeup tutorial', 'easy halloween'], 'views': 94113, 'likes': 4241, 'dislikes': 127, 'comment_total': 218, 'thumbnail_link': 'https://i.ytimg.com/vi/rWKz0ZC_G6U/default.jpg', 'date': 7.1, 'kind': 'youtube#videoCategory', 'etag': '"m2yskBQFythfE4irbTIeOgYYfBU/xId8RX7vRN8rqkbYZbNIytUQDRo"', 'channelId': 'UCBR8-60-B28hp2BmDPdntcQ', 'category': 'People & Blogs', 'assignable': True}
-----
{'_id': ObjectId('5fc5007c350898a3d9107bce'), 'video_id': 'ziwI9E9xF4s', 'title_x': 'Warriors Training Camp & Ride Along With KD', 'channel_title': 'Kevin Durant', 'category_id': 22, 'tags': ['kd', 'kevin durant', 'warriors', 'golde

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



## Question 4

In [123]:
max = collection.find({},{"views","title_x"}).sort("views",-1)

In [124]:
for i in max :
    print("----")
    print(i)

----
{'_id': ObjectId('5fc5007c350898a3d910861a'), 'title_x': "BTS (방탄소년단) 'DNA' Official MV", 'views': 41500672}
----
{'_id': ObjectId('5fc5007c350898a3d9108606'), 'title_x': "BTS (방탄소년단) 'DNA' Official MV", 'views': 38013692}
----
{'_id': ObjectId('5fc5007c350898a3d91084f1'), 'title_x': 'ZAYN - Dusk Till Dawn ft. Sia', 'views': 36323498}
----
{'_id': ObjectId('5fc5007c350898a3d91076e4'), 'title_x': 'Eminem Rips Donald Trump In BET Hip Hop Awards Freestyle Cypher', 'views': 33191594}
----
{'_id': ObjectId('5fc5007c350898a3d91076b8'), 'title_x': 'Eminem Rips Donald Trump In BET Hip Hop Awards Freestyle Cypher', 'views': 32512343}
----
{'_id': ObjectId('5fc5007c350898a3d9108620'), 'title_x': 'Shakira - Perro Fiel (Official Video) ft. Nicky Jam', 'views': 32136948}
----
{'_id': ObjectId('5fc5007c350898a3d910768a'), 'title_x': 'Eminem Rips Donald Trump In BET Hip Hop Awards Freestyle Cypher', 'views': 31636010}
----
{'_id': ObjectId('5fc5007c350898a3d91085e7'), 'title_x': "BTS (방탄소년단) 'DN

{'_id': ObjectId('5fc5007c350898a3d9107efa'), 'title_x': 'I Buy My Boyfriends Outfits', 'views': 2575442}
----
{'_id': ObjectId('5fc5007c350898a3d9107dee'), 'title_x': 'Worst Nap Ever | Lele Pons', 'views': 2572619}
----
{'_id': ObjectId('5fc5007c350898a3d9108766'), 'title_x': 'Sam Smith - Too Good At Goodbyes (Live From Hackney Round Chapel)', 'views': 2571370}
----
{'_id': ObjectId('5fc5007c350898a3d91080e8'), 'title_x': 'Film Theory: Did Rick CLONE Beth - SOLVED! (Rick and Morty)', 'views': 2570340}
----
{'_id': ObjectId('5fc5007c350898a3d9107a62'), 'title_x': 'What If the Whale Swallowed You Alive?', 'views': 2565878}
----
{'_id': ObjectId('5fc5007c350898a3d910895e'), 'title_x': 'John Legend - Penthouse Floor ft. Chance the Rapper', 'views': 2558262}
----
{'_id': ObjectId('5fc5007c350898a3d91079e6'), 'title_x': 'The Try Guys Get Makeovers From High School Girls', 'views': 2557131}
----
{'_id': ObjectId('5fc5007c350898a3d91079b6'), 'title_x': 'I Bought An Entire Outfit Blindfolded',

----
{'_id': ObjectId('5fc5007c350898a3d91089a5'), 'title_x': 'Martin Garrix & Matisse & Sadko - Forever (Official Music Video)', 'views': 1699530}
----
{'_id': ObjectId('5fc5007c350898a3d9107b17'), 'title_x': 'i have a problem', 'views': 1695300}
----
{'_id': ObjectId('5fc5007c350898a3d9107bf4'), 'title_x': 'QATAR AIRWAYS A350 BUSINESS CLASS REVIEW; INCREDIBLE', 'views': 1693261}
----
{'_id': ObjectId('5fc5007c350898a3d9107491'), 'title_x': 'We Need To Talk About The Las Vegas Shooting...', 'views': 1693031}
----
{'_id': ObjectId('5fc5007c350898a3d9107eed'), 'title_x': 'Fast Food Hot Sauce Taste Test', 'views': 1692926}
----
{'_id': ObjectId('5fc5007c350898a3d910804c'), 'title_x': 'Honest Trailers - The Mummy (2017)', 'views': 1692235}
----
{'_id': ObjectId('5fc5007c350898a3d9108067'), 'title_x': 'THE SHAPE OF WATER - Red Band Trailer', 'views': 1689730}
----
{'_id': ObjectId('5fc5007c350898a3d9108690'), 'title_x': "Jason Derulo - If I'm Lucky Part 1 (Official Music Video)", 'views': 

{'_id': ObjectId('5fc5007c350898a3d91089f1'), 'title_x': 'Storm Chaser Battles Hurricane Irma’s Powerful Winds | NBC News', 'views': 1178955}
----
{'_id': ObjectId('5fc5007c350898a3d910771c'), 'title_x': "I'M HOLO INSIDE! Holographic scar makeup ft. Glam&Gore", 'views': 1177430}
----
{'_id': ObjectId('5fc5007c350898a3d9107581'), 'title_x': 'The Struggles of Watching ASMR', 'views': 1175927}
----
{'_id': ObjectId('5fc5007c350898a3d910876c'), 'title_x': 'Demi Lovato - Sorry Not Sorry (Vevo X Demi Lovato)', 'views': 1174269}
----
{'_id': ObjectId('5fc5007c350898a3d910853e'), 'title_x': 'Machine Gun Kelly - Let You Go', 'views': 1173691}
----
{'_id': ObjectId('5fc5007c350898a3d9107f84'), 'title_x': 'The Fire Whisperer - Cyanide & Happiness Shorts', 'views': 1172915}
----
{'_id': ObjectId('5fc5007c350898a3d9107ea5'), 'title_x': 'Famous YouTubers | My Parents React (Ep. 26)', 'views': 1171308}
----
{'_id': ObjectId('5fc5007c350898a3d91086d9'), 'title_x': 'RAPPING FOR A JOB AT VAYNERMEDIA', '

{'_id': ObjectId('5fc5007c350898a3d9107956'), 'title_x': 'Whats inside a LIFE SAVING Watch?', 'views': 888148}
----
{'_id': ObjectId('5fc5007c350898a3d9107b62'), 'title_x': "Las Vegas shooting: GMB SLAMMED over 'unprofessional' Mariah Carey interview", 'views': 888010}
----
{'_id': ObjectId('5fc5007c350898a3d910761e'), 'title_x': 'NY Comic-Con Official Trailer: THE X-FILES | Season 11 | THE X-FILES', 'views': 887297}
----
{'_id': ObjectId('5fc5007c350898a3d91075f7'), 'title_x': 'Spill Your Guts or Fill Your Guts w/ Charlie Puth, Josh Gad, Michelle Dockery & Rachel Bloom', 'views': 886790}
----
{'_id': ObjectId('5fc5007c350898a3d91079f0'), 'title_x': 'Alexa: Guess My Number', 'views': 885969}
----
{'_id': ObjectId('5fc5007c350898a3d9107ec9'), 'title_x': 'Clueless Gamer: Shadow Of War With Kumail Nanjiani  - CONAN on TBS', 'views': 885381}
----
{'_id': ObjectId('5fc5007c350898a3d9107e14'), 'title_x': 'Road Trip with The Dolan Twins', 'views': 884418}
----
{'_id': ObjectId('5fc5007c350898

...

{'_id': ObjectId('5fc5007c350898a3d9107ade'), 'title_x': "MY GIRLFRIEND'S GAY FRIEND", 'views': 109978}
----
{'_id': ObjectId('5fc5007c350898a3d910841e'), 'title_x': 'My EXCITING News!!', 'views': 109892}
----
{'_id': ObjectId('5fc5007c350898a3d910839a'), 'title_x': 'How To LEVEL UP Hot Chocolate Fudge Sauce', 'views': 109868}
----
{'_id': ObjectId('5fc5007c350898a3d910896f'), 'title_x': 'LP - Lost On You (A Night at The McKittrick Hotel)', 'views': 109853}
----
{'_id': ObjectId('5fc5007c350898a3d9107697'), 'title_x': 'EXTREME PUMPKIN CARVING | for National Coming Out Day', 'views': 109832}
----
{'_id': ObjectId('5fc5007c350898a3d9108b61'), 'title_x': 'Vegas victim reunited with man who saved her', 'views': 109754}
----
{'_id': ObjectId('5fc5007c350898a3d91080e4'), 'title_x': 'Guardians of the Galaxy Vol. 2 | VFX Breakdown | Framestore', 'views': 109739}
----
{'_id': ObjectId('5fc5007c350898a3d9108d30'), 'title_x': "Jeremy Lin addresses Kenyon Martin's comments about his dreads", 'view

{'_id': ObjectId('5fc5007c350898a3d9108d6b'), 'title_x': "Taylor Twellman says there's an 'arrogance' to the U.S. men's soccer team | SportsCenter | ESPN", 'views': 72446}
----
{'_id': ObjectId('5fc5007c350898a3d91087d9'), 'title_x': 'POKÉMON POWER | Songify This', 'views': 72414}
----
{'_id': ObjectId('5fc5007c350898a3d9108862'), 'title_x': 'Hunter Hayes - You Should Be Loved (Official Audio)', 'views': 72301}
----
{'_id': ObjectId('5fc5007c350898a3d9107607'), 'title_x': 'EXTREME PUMPKIN CARVING | for National Coming Out Day', 'views': 72299}
----
{'_id': ObjectId('5fc5007c350898a3d9108e6a'), 'title_x': 'AT&T: The Company Behind the Telephone', 'views': 72219}
----
{'_id': ObjectId('5fc5007c350898a3d9108f34'), 'title_x': 'Behind the Scenes Subaru WRX STI Type RA NBR Special Nurburgring', 'views': 72124}
----
{'_id': ObjectId('5fc5007c350898a3d9107cfd'), 'title_x': 'Homemade Nintendo Switch- NinTIMdo RP', 'views': 72102}
----
{'_id': ObjectId('5fc5007c350898a3d91088be'), 'title_x': 'Ch

----
{'_id': ObjectId('5fc5007c350898a3d910851b'), 'title_x': 'Chris Young - Losing Sleep', 'views': 47369}
----
{'_id': ObjectId('5fc5007c350898a3d9108604'), 'title_x': 'björk: the gate', 'views': 47345}
----
{'_id': ObjectId('5fc5007c350898a3d91083ea'), 'title_x': 'How to Make Pusheen Brownie Pops! 💕', 'views': 47204}
----
{'_id': ObjectId('5fc5007c350898a3d9107bbd'), 'title_x': 'HOA fight over WWII tank', 'views': 47100}
----
{'_id': ObjectId('5fc5007c350898a3d910741d'), 'title_x': 'New Thor: Ragnarok International Trailer Featuring More Hela - Movie Talk', 'views': 47089}
----
{'_id': ObjectId('5fc5007c350898a3d910904b'), 'title_x': 'Blue Planet II Trailer 2 - BBC Earth', 'views': 47077}
----
{'_id': ObjectId('5fc5007c350898a3d9108257'), 'title_x': 'Does the Ultra Boost Get Less Comfortable?', 'views': 47049}
----
{'_id': ObjectId('5fc5007c350898a3d91073db'), 'title_x': "Strike Back - Marvel's Inhumans Trailer", 'views': 47042}
----
{'_id': ObjectId('5fc5007c350898a3d910852c'), 'ti

{'_id': ObjectId('5fc5007c350898a3d9108a06'), 'title_x': 'Car Hits Cyclist in East Flatbush', 'views': 16376}
----
{'_id': ObjectId('5fc5007c350898a3d910742e'), 'title_x': 'Will Sterling K Brown Be Part Of ‘American Crime Story: Katrina’? | WWHL', 'views': 16370}
----
{'_id': ObjectId('5fc5007c350898a3d910819f'), 'title_x': '10 Hour Test On These 5 Cult Beauty Buys | Full Face First Impressions | Beauty With Mi', 'views': 16296}
----
{'_id': ObjectId('5fc5007c350898a3d910889f'), 'title_x': 'Darius Rucker - Bring It On (Audio)', 'views': 16268}
----
{'_id': ObjectId('5fc5007c350898a3d9108b5b'), 'title_x': 'Trump in San Juan: Maria has thrown US budget out of whack', 'views': 16252}
----
{'_id': ObjectId('5fc5007c350898a3d9108b11'), 'title_x': 'Fox News blames CNN for mass shootings', 'views': 16229}
----
{'_id': ObjectId('5fc5007c350898a3d9107c19'), 'title_x': 'Jacob Sartorius Gives RAW Interview', 'views': 16195}
----
{'_id': ObjectId('5fc5007c350898a3d9108ad7'), 'title_x': 'Playboy fo

----
{'_id': ObjectId('5fc5007c350898a3d9108c23'), 'title_x': 'AIRFRAME: F-22 Raptor', 'views': 2182}
----
{'_id': ObjectId('5fc5007c350898a3d91074fe'), 'title_x': 'Best Tom Petty Interview Ever', 'views': 2143}
----
{'_id': ObjectId('5fc5007c350898a3d9107ba6'), 'title_x': 'TremorFreeMe suppression results', 'views': 2136}
----
{'_id': ObjectId('5fc5007c350898a3d9107c3f'), 'title_x': 'Issa Rae & Yvonne Orji Throw The Blackest Party of 2017 - [#LemonPepperShawties]', 'views': 2075}
----
{'_id': ObjectId('5fc5007c350898a3d9107a95'), 'title_x': 'ATL100 - Movie Theater Preview', 'views': 2070}
----
{'_id': ObjectId('5fc5007c350898a3d9107b86'), 'title_x': 'TremorFreeMe suppression results', 'views': 2050}
----
{'_id': ObjectId('5fc5007c350898a3d91080ca'), 'title_x': "Detroit's unaffordable water hints at a U.S. crisis to come", 'views': 2036}
----
{'_id': ObjectId('5fc5007c350898a3d9107c1e'), 'title_x': 'Issa Rae & Yvonne Orji Throw The Blackest Party of 2017 - [#LemonPepperShawties]', 'vie

## Question 5

In [133]:
MeanGroup = collection.aggregate([{"$group":{"_id":"$category","moyenne":{"$avg":"$views"}}}])

In [134]:
list(MeanGroup)

[{'_id': 'Travel & Events', 'moyenne': 464041.0833333333},
 {'_id': 'Gaming', 'moyenne': 681081.8170731707},
 {'_id': 'Sports', 'moyenne': 728434.3243902439},
 {'_id': 'Autos & Vehicles', 'moyenne': 607693.8706896552},
 {'_id': 'People & Blogs', 'moyenne': 971532.7573696146},
 {'_id': 'Film & Animation', 'moyenne': 1039472.6560846561},
 {'_id': 'Music', 'moyenne': 1176553.612},
 {'_id': 'Pets & Animals', 'moyenne': 651404.3879310344},
 {'_id': 'Howto & Style', 'moyenne': 537665.1806674339},
 {'_id': 'Comedy', 'moyenne': 1240073.294039735},
 {'_id': 'Science & Technology', 'moyenne': 924730.548828125},
 {'_id': 'News & Politics', 'moyenne': 540955.5569823436},
 {'_id': 'Entertainment', 'moyenne': 1154868.4397251718},
 {'_id': 'Nonprofits & Activism', 'moyenne': 1110334.2142857143},
 {'_id': 'Shows', 'moyenne': 8492.5},
 {'_id': 'Education', 'moyenne': 547582.4700598803}]

## Question 6 

In [143]:
MaxCh = collection.aggregate([{"$group":{"_id":"$channel_title","moyenne":{"$avg":"$likes"}}},{"$sort":{"moyenne":-1}}])

In [144]:
list(MaxCh)

[{'_id': 'ZaynVEVO', 'moyenne': 1431683.0},
 {'_id': 'ibighit', 'moyenne': 1371766.25},
 {'_id': 'melanie martinez', 'moyenne': 911871.5},
 {'_id': 'BETNetworks', 'moyenne': 769687.625},
 {'_id': 'jypentertainment', 'moyenne': 758826.6666666666},
 {'_id': 'Logan Paul Vlogs', 'moyenne': 653443.5384615385},
 {'_id': 'Wengie', 'moyenne': 567235.2},
 {'_id': 'Alesso', 'moyenne': 509417.28571428574},
 {'_id': 'PewDiePie', 'moyenne': 508647.8},
 {'_id': 'shakiraVEVO', 'moyenne': 434302.14285714284},
 {'_id': 'Ed Sheeran', 'moyenne': 395654.1666666667},
 {'_id': 'Dude Perfect', 'moyenne': 389697.1111111111},
 {'_id': 'Conor Maynard', 'moyenne': 389273.0},
 {'_id': 'TaylorSwiftVEVO', 'moyenne': 367455.6666666667},
 {'_id': 'Liza Koshy', 'moyenne': 365146.9583333333},
 {'_id': 'Linkin Park', 'moyenne': 356475.7272727273},
 {'_id': 'jbalvinVEVO', 'moyenne': 345130.4285714286},
 {'_id': 'Primitive Technology', 'moyenne': 340659.25},
 {'_id': 'Gabbie Hanna', 'moyenne': 339488.0},
 {'_id': 'Bhad Bh